In [1]:
import numpy as np
import tensorflow as tf
import librosa
import os
import itertools
from jupyterplot import ProgressPlot


In [2]:
# Hack to get it to work with RTX 2000 cards
gpus = tf.config.experimental.list_physical_devices('GPU')
for gpu in gpus:
  tf.config.experimental.set_memory_growth(gpu, True)

2021-11-20 11:18:12.194775: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2021-11-20 11:18:12.200405: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2021-11-20 11:18:12.200950: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero


In [3]:
# Load a file
dataset_dir = './Baggins_Music/'
music_filenames = os.listdir(dataset_dir)

In [4]:
song_np, sr = librosa.load(dataset_dir+music_filenames[0], mono=False)
song_np = np.transpose(song_np)

/home/bij/anaconda3/envs/MusicAnalyzer/lib/python3.8/site-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")


NameError: name 'y' is not defined

In [ ]:
# Papers and resources
# WaveNet paper https://arxiv.org/pdf/1609.03499.pdf
# WaveNet AutoEncoder paper (instrument decomp): https://arxiv.org/pdf/1704.01279.pdf
# NSynth: https://magenta.tensorflow.org/nsynth
# WaveNet implementation: https://github.com/ibab/tensorflow-wavenet

In [38]:
def dilconv_outlen(input_len, dil_rate, kernel_size):
    return input_len - (kernel_size-1)*dil_rate

def calc_num_layers(tgt_output_len, input_len, dil_rate, kernel_size):
    '''
    Calculates how many encoder layers are required to get to the target output length
    from a given input length, given a few conv1d params. 
    '''
    num_layers = (input_len - tgt_output_len)/((kernel_size-1)*dil_rate)
    return num_layers

# Define the audio autoencoder 
class AudioAutoEncoder(tf.keras.Model):

    def __init__(self, input_dur=1, sample_rate=22050):
        '''
        input_dur: duration of input (in seconds)
        sample_rate: sampling frequency of input audio (in hz) 
        '''
        super(AudioAutoEncoder, self).__init__()
        self.input_len = input_dur*sample_rate
        self.sample_rate = sample_rate

        # A loss function
        self.mse = tf.keras.losses.MeanSquaredError()
        # An optimizer
        #self.optim = tf.keras.optimizers.SGD(learning_rate=0.1, momentum=0.0, nesterov=False, name='SGD')
        self.optim = tf.keras.optimizers.Adam(learning_rate=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-07, amsgrad=False,name='Adam')


        # Calculate how many layers we need for a receptive field to cover the whole sample
        self.dil_rate = 100
        self.z_len = 1024
        kern_size = 16
        self.num_filts = 16
        self.num_enc_lyrs = int(calc_num_layers(self.z_len, self.input_len, self.dil_rate, kern_size))
        
        
        print('Num Layers: ', self.num_enc_lyrs)
        
        # Setup encoder layers
        self.enc_lyrs = []
        for lyr_num in range(self.num_enc_lyrs):
            if(lyr_num+1 >= self.num_enc_lyrs):
                num_filts = 2
            else:
                num_filts = self.num_filts
            self.enc_lyrs += [tf.keras.layers.Conv1D(filters=num_filts, 
                                                     kernel_size=kern_size, 
                                                     strides=1, 
                                                     dilation_rate=self.dil_rate, 
                                                     activation='relu')]
        
        # Setup encoder layers
        self.dec_lyrs = []
        for lyr_num in range(self.num_enc_lyrs):
            if(lyr_num+1 >= self.num_enc_lyrs):
                num_filts = 2
            else:
                num_filts = self.num_filts
            print(num_filts)
            self.dec_lyrs += [tf.keras.layers.Conv1DTranspose(filters=num_filts, 
                                                     kernel_size=kern_size, 
                                                     strides=1, 
                                                     dilation_rate=self.dil_rate, 
                                                     activation='relu')]
        

        
    def encoder(self, x):
        for idx,lyr in enumerate(self.enc_lyrs):
            #print('Layer: ', idx, '\t', x.shape, idx, '/', len(self.enc_lyrs))
            x = lyr(x)
        return x
    
    def decoder(self, x):
        for idx,lyr in enumerate(self.dec_lyrs):
            #print('Layer: ', idx, '\t', x.shape, idx, '/', len(self.dec_lyrs))
            x = lyr(x)
        return x
    
    def calc_loss(self, x_hat, x):
        loss = self.mse(x, x_hat)
        return loss
        
    def call(self, inputs):
        z = self.encoder(inputs)
        #print('Z shape: ', z.shape)
        x_hat = self.decoder(z)
        
        return x_hat


In [39]:
auto_encoder = AudioAutoEncoder()

Num Layers:  14
16
16
16
16
16
16
16
16
16
16
16
16
16
2


NameError: name 'kwargs' is not defined

In [8]:
# Prep the dataset
ds_num_samples = int(len(song_np)/auto_encoder.input_len)
song_ds = song_np[0:auto_encoder.input_len*ds_num_samples]
song_ds = np.reshape(song_ds, (ds_num_samples, -1, 2))
song_ds.shape

(3111, 22050, 2)

In [29]:
class Smoother:
    def __init__(self, buf_len=15):
        self.buffer = []
        self.max_len = buf_len
    def smooth(self, x):
        self.buffer += [x]
        if(len(self.buffer) > self.max_len):
            self.buffer.pop(0)
            
        return np.mean(np.array(self.buffer))

In [40]:
# Create the dataset

print(ds_num_samples)
batch_size = 16
#batch_size = 64

# For plotting loss
pp = ProgressPlot()
# Smoother for smoothing
smoother = Smoother(buf_len=15)

# Train the autoencoder
for step in itertools.count():
    # Get the batch
    batch_idxs = np.random.randint(0, ds_num_samples, size=batch_size)
    x = song_ds[batch_idxs]

    # Put batch through model
    
    with tf.GradientTape() as t:
        x_hat = auto_encoder(x)
        # Get Loss
        loss_recon = auto_encoder.calc_loss(x_hat, x)
        pp.update(float(smoother.smooth(loss_recon.numpy())))
        print('Step {0:8d}\tLoss: {1:3.4f}'.format(step, loss_recon.numpy()))
        grads = t.gradient(loss_recon, auto_encoder.variables)
        
    # Backprop grads
    auto_encoder.optim.apply_gradients(zip(grads, auto_encoder.variables))
    
    
    

3111


<IPython.core.display.Javascript object>

Step        0	Loss: 0.0265
Step        1	Loss: 0.0196
Step        2	Loss: 0.0260
Step        3	Loss: 0.0257
Step        4	Loss: 0.0286
Step        5	Loss: 0.0255
Step        6	Loss: 0.0292
Step        7	Loss: 0.0326
Step        8	Loss: 0.0246
Step        9	Loss: 0.0221
Step       10	Loss: 0.0174
Step       11	Loss: 0.0191
Step       12	Loss: 0.0294
Step       13	Loss: 0.0301
Step       14	Loss: 0.0171
Step       15	Loss: 0.0215
Step       16	Loss: 0.0194
Step       17	Loss: 0.0267
Step       18	Loss: 0.0260
Step       19	Loss: 0.0230
Step       20	Loss: 0.0230
Step       21	Loss: 0.0217
Step       22	Loss: 0.0214
Step       23	Loss: 0.0245
Step       24	Loss: 0.0242
Step       25	Loss: 0.0283
Step       26	Loss: 0.0247
Step       27	Loss: 0.0235
Step       28	Loss: 0.0280
Step       29	Loss: 0.0225
Step       30	Loss: 0.0237
Step       31	Loss: 0.0231
Step       32	Loss: 0.0303
Step       33	Loss: 0.0243
Step       34	Loss: 0.0207
Step       35	Loss: 0.0374
Step       36	Loss: 0.0297
S

Step      304	Loss: 0.0237
Step      305	Loss: 0.0197
Step      306	Loss: 0.0280
Step      307	Loss: 0.0234
Step      308	Loss: 0.0199
Step      309	Loss: 0.0193
Step      310	Loss: 0.0236
Step      311	Loss: 0.0214
Step      312	Loss: 0.0266
Step      313	Loss: 0.0215
Step      314	Loss: 0.0209
Step      315	Loss: 0.0246
Step      316	Loss: 0.0259
Step      317	Loss: 0.0244
Step      318	Loss: 0.0288
Step      319	Loss: 0.0177
Step      320	Loss: 0.0227
Step      321	Loss: 0.0293
Step      322	Loss: 0.0282
Step      323	Loss: 0.0281
Step      324	Loss: 0.0299
Step      325	Loss: 0.0309
Step      326	Loss: 0.0270
Step      327	Loss: 0.0261
Step      328	Loss: 0.0261
Step      329	Loss: 0.0257
Step      330	Loss: 0.0266
Step      331	Loss: 0.0301
Step      332	Loss: 0.0349
Step      333	Loss: 0.0215
Step      334	Loss: 0.0260
Step      335	Loss: 0.0281
Step      336	Loss: 0.0356
Step      337	Loss: 0.0261
Step      338	Loss: 0.0240
Step      339	Loss: 0.0189
Step      340	Loss: 0.0242
S

Step      608	Loss: 0.0262
Step      609	Loss: 0.0229
Step      610	Loss: 0.0208
Step      611	Loss: 0.0234
Step      612	Loss: 0.0327
Step      613	Loss: 0.0258
Step      614	Loss: 0.0279
Step      615	Loss: 0.0297
Step      616	Loss: 0.0236
Step      617	Loss: 0.0204
Step      618	Loss: 0.0215
Step      619	Loss: 0.0234
Step      620	Loss: 0.0195
Step      621	Loss: 0.0244
Step      622	Loss: 0.0271
Step      623	Loss: 0.0250
Step      624	Loss: 0.0307
Step      625	Loss: 0.0218
Step      626	Loss: 0.0284
Step      627	Loss: 0.0221
Step      628	Loss: 0.0246
Step      629	Loss: 0.0228
Step      630	Loss: 0.0304
Step      631	Loss: 0.0223
Step      632	Loss: 0.0346
Step      633	Loss: 0.0188
Step      634	Loss: 0.0254
Step      635	Loss: 0.0262
Step      636	Loss: 0.0228
Step      637	Loss: 0.0262
Step      638	Loss: 0.0293
Step      639	Loss: 0.0334
Step      640	Loss: 0.0271
Step      641	Loss: 0.0193
Step      642	Loss: 0.0214
Step      643	Loss: 0.0312
Step      644	Loss: 0.0229
S

...

Step   213104	Loss: 0.0243
Step   213105	Loss: 0.0291
Step   213106	Loss: 0.0220
Step   213107	Loss: 0.0308
Step   213108	Loss: 0.0263
Step   213109	Loss: 0.0253
Step   213110	Loss: 0.0245
Step   213111	Loss: 0.0250
Step   213112	Loss: 0.0259
Step   213113	Loss: 0.0177
Step   213114	Loss: 0.0262
Step   213115	Loss: 0.0229
Step   213116	Loss: 0.0313
Step   213117	Loss: 0.0253
Step   213118	Loss: 0.0273
Step   213119	Loss: 0.0320
Step   213120	Loss: 0.0209
Step   213121	Loss: 0.0224
Step   213122	Loss: 0.0317
Step   213123	Loss: 0.0317
Step   213124	Loss: 0.0181
Step   213125	Loss: 0.0265
Step   213126	Loss: 0.0235
Step   213127	Loss: 0.0244
Step   213128	Loss: 0.0315
Step   213129	Loss: 0.0180
Step   213130	Loss: 0.0306
Step   213131	Loss: 0.0280
Step   213132	Loss: 0.0247
Step   213133	Loss: 0.0217
Step   213134	Loss: 0.0202
Step   213135	Loss: 0.0206
Step   213136	Loss: 0.0201
Step   213137	Loss: 0.0295
Step   213138	Loss: 0.0310
Step   213139	Loss: 0.0208
Step   213140	Loss: 0.0204
S

Step   213408	Loss: 0.0324
Step   213409	Loss: 0.0297
Step   213410	Loss: 0.0261
Step   213411	Loss: 0.0195
Step   213412	Loss: 0.0362
Step   213413	Loss: 0.0209
Step   213414	Loss: 0.0295
Step   213415	Loss: 0.0210
Step   213416	Loss: 0.0259
Step   213417	Loss: 0.0213
Step   213418	Loss: 0.0286
Step   213419	Loss: 0.0295
Step   213420	Loss: 0.0202
Step   213421	Loss: 0.0302
Step   213422	Loss: 0.0211
Step   213423	Loss: 0.0254
Step   213424	Loss: 0.0348
Step   213425	Loss: 0.0223
Step   213426	Loss: 0.0260
Step   213427	Loss: 0.0318
Step   213428	Loss: 0.0311
Step   213429	Loss: 0.0218
Step   213430	Loss: 0.0248
Step   213431	Loss: 0.0237
Step   213432	Loss: 0.0228
Step   213433	Loss: 0.0306
Step   213434	Loss: 0.0278
Step   213435	Loss: 0.0245
Step   213436	Loss: 0.0270
Step   213437	Loss: 0.0219
Step   213438	Loss: 0.0211
Step   213439	Loss: 0.0293
Step   213440	Loss: 0.0269
Step   213441	Loss: 0.0268
Step   213442	Loss: 0.0237
Step   213443	Loss: 0.0287
Step   213444	Loss: 0.0266
S

Step   213712	Loss: 0.0315
Step   213713	Loss: 0.0187
Step   213714	Loss: 0.0275
Step   213715	Loss: 0.0253
Step   213716	Loss: 0.0210
Step   213717	Loss: 0.0323
Step   213718	Loss: 0.0225
Step   213719	Loss: 0.0250
Step   213720	Loss: 0.0247
Step   213721	Loss: 0.0284
Step   213722	Loss: 0.0270
Step   213723	Loss: 0.0244
Step   213724	Loss: 0.0244
Step   213725	Loss: 0.0268
Step   213726	Loss: 0.0237
Step   213727	Loss: 0.0265
Step   213728	Loss: 0.0211
Step   213729	Loss: 0.0221
Step   213730	Loss: 0.0236
Step   213731	Loss: 0.0326
Step   213732	Loss: 0.0321
Step   213733	Loss: 0.0303
Step   213734	Loss: 0.0310
Step   213735	Loss: 0.0265
Step   213736	Loss: 0.0272
Step   213737	Loss: 0.0282
Step   213738	Loss: 0.0252
Step   213739	Loss: 0.0325
Step   213740	Loss: 0.0261
Step   213741	Loss: 0.0289
Step   213742	Loss: 0.0225
Step   213743	Loss: 0.0319
Step   213744	Loss: 0.0237
Step   213745	Loss: 0.0254
Step   213746	Loss: 0.0236
Step   213747	Loss: 0.0190
Step   213748	Loss: 0.0300
S

Step   214016	Loss: 0.0152
Step   214017	Loss: 0.0222
Step   214018	Loss: 0.0284
Step   214019	Loss: 0.0248
Step   214020	Loss: 0.0289
Step   214021	Loss: 0.0333
Step   214022	Loss: 0.0306
Step   214023	Loss: 0.0262
Step   214024	Loss: 0.0226
Step   214025	Loss: 0.0245
Step   214026	Loss: 0.0270
Step   214027	Loss: 0.0217
Step   214028	Loss: 0.0253
Step   214029	Loss: 0.0247
Step   214030	Loss: 0.0165
Step   214031	Loss: 0.0344
Step   214032	Loss: 0.0272
Step   214033	Loss: 0.0319
Step   214034	Loss: 0.0217
Step   214035	Loss: 0.0295
Step   214036	Loss: 0.0305
Step   214037	Loss: 0.0235
Step   214038	Loss: 0.0261
Step   214039	Loss: 0.0262
Step   214040	Loss: 0.0222
Step   214041	Loss: 0.0282
Step   214042	Loss: 0.0302
Step   214043	Loss: 0.0208
Step   214044	Loss: 0.0198
Step   214045	Loss: 0.0261
Step   214046	Loss: 0.0269
Step   214047	Loss: 0.0264
Step   214048	Loss: 0.0280
Step   214049	Loss: 0.0234
Step   214050	Loss: 0.0311
Step   214051	Loss: 0.0224
Step   214052	Loss: 0.0221
S

KeyboardInterrupt: 

In [22]:
smoother = Smoother(buf_len=12)